In [1]:
# Plot all buoys in atlantic

In [2]:
import folium
from folium import plugins
from argopy import IndexFetcher as ArgoIndexFetcher
import numpy as np
import cartopy
import pandas as pd
import datetime


In [3]:
import matplotlib.pyplot as plt
import matplotlib

In [4]:
import warnings 
#warnings.filterwarnings(action='once')
warnings.filterwarnings('ignore')

In [5]:
# pd.set_option('display.max_colwidth', None)
list_gulf_of_mexico = [4901598, 4902349, 4902350, 4902351, 4902352, 4902915, 4902917, 4902916, 4902914, 
                       6902854, 6902855, 6902852, 6902851, 6902853, 6902849, 4903237, 4903232, 4903240, 
                       4903238, 4903249, 4903255, 4903259, 4903256, 4903250, 4903251, 4903248, 4903253, 
                       4903254, 4903276, 4903278, 4903277, 4903279, 4903355, 4903353, 4903354, 4903356]
list_gulf_of_mexico.sort()
display(list_gulf_of_mexico)

[4901598,
 4902349,
 4902350,
 4902351,
 4902352,
 4902914,
 4902915,
 4902916,
 4902917,
 4903232,
 4903237,
 4903238,
 4903240,
 4903248,
 4903249,
 4903250,
 4903251,
 4903253,
 4903254,
 4903255,
 4903256,
 4903259,
 4903276,
 4903277,
 4903278,
 4903279,
 4903353,
 4903354,
 4903355,
 4903356,
 6902849,
 6902851,
 6902852,
 6902853,
 6902854,
 6902855]

In [6]:
#num_2021_deploy = 4903350
#idx_small = ArgoIndexFetcher(cache=True).float([num_2021_deploy])
#df_buoy = idx_small.to_dataframe()

idx_gulf_mexico = ArgoIndexFetcher(cache=True).float(list_gulf_of_mexico)
print("Current date and time: ", datetime.datetime.now())

Current date and time:  2021-06-09 01:29:09.157807


In [7]:
index_loader = ArgoIndexFetcher(cache=True)
idx = index_loader.region([-80, -39, 0, 50, '2020-06-01', '2021-07'])

In [8]:
df_buoy = idx.to_dataframe()
print("Current date and time: ", datetime.datetime.now())
#df_buoy.to_csv('gulf_mexico.csv')

Current date and time:  2021-06-09 01:30:04.890275


In [15]:
df_buoy[df_buoy.wmo == 4902916]

Empty DataFrame
Columns: [file, date, longitude, latitude, ocean, profiler_code, institution_code, date_update, wmo, institution, profiler, longlat]
Index: []

In [25]:
list_buoy_ids = df_buoy.wmo.unique()
list_buoy_ids

array([6902957, 6901215, 4903036, 4902121, 4903049, 4902441, 3901686,
       6903720, 6902843, 4902342, 4902344, 4903048, 6902966, 6903715,
       6901182, 4902112, 3901604, 4903246, 6901145, 4901592, 6902675,
       4903244, 3901603, 4903226, 7900529, 6902766, 4901798, 4902339,
       1901713, 6902878, 6901183, 4901630, 6902745, 6902659, 4902100,
       4901591, 6902958, 3901980, 5904664, 4901765, 3901987, 3901979,
       3901986, 4902354, 4902104, 4902109, 3902166, 6902658, 4903214,
       6902714, 6902713, 6902964, 3901601, 4902110, 4902455, 5904772,
       4902456, 4902424, 3901605, 3901658, 4901626, 3901857, 3901859,
       4901710, 3901971, 4902108, 4902912, 6901144, 1901731, 4902913,
       4902345, 6901195, 4901587, 4903054, 3901654, 6900894, 4902114,
       4902393, 4902394, 4902927, 4902324, 4902910, 6901931, 4901701,
       3901684, 4903219, 4903245, 5904669, 3901657, 3901640, 3901656,
       4901700, 4902348, 4902102, 6902711, 4901631, 3901637, 4902470,
       4902467, 4903

In [16]:
 df_buoy = df_buoy.dropna(subset=['latitude', 'longitude'])

In [17]:
print("Current date and time: ", datetime.datetime.now())
df_buoy['longlat'] = list(zip(df_buoy.longitude, df_buoy.latitude)) 
df_timelapse = df_buoy[['longlat', 'date', 'date_update', 'wmo']]

Current date and time:  2021-06-09 01:30:24.607658


In [38]:
start_longlat = (-88.3, 26.5)
start_longlat = (26.5, -88.3 )
start_longlat = (25, -55)

##  set time limits to restrict number of buoys handled while debugging

In [19]:
TIME_START = '2021-01-01'
TIME_END = '2021-06-30'

In [20]:
TIME_START = '1970-01-05'
TIME_END = '2021-06-30'

In [21]:
NaT_fill = np.datetime64(0, 's')

In [26]:
features = []
#cmap = plt.cm.get_cmap("tab20")#, len(list_gulf_of_mexico))
num_colors = len(list_buoy_ids)
cmap = matplotlib.cm.get_cmap('prism', num_colors)
NaT_fill = 0 
gps_fill = -99
    
for ith_buoy, buoy in enumerate(list_buoy_ids):
    buoy_df = df_timelapse[ (df_timelapse.wmo == buoy) & (df_timelapse.date_update > TIME_START) & (df_timelapse.date_update < TIME_END)]
    buoy_df['line_coords'] = list(zip(
        buoy_df['longlat'].shift(fill_value = gps_fill), 
        buoy_df['longlat']))
    
    buoy_df = buoy_df.sort_values(by=['wmo','date'])
    
    buoy_df['str_date'] = buoy_df['date'].dt.strftime('%Y-%m-%d %H:%M:%S')
    buoy_df['line_times'] = list(zip(
        buoy_df['str_date'].shift(fill_value = NaT_fill) , 
        buoy_df['str_date']
    ))
    
    for _, row in buoy_df.iterrows():
        if row.line_times[0] == 0:
            #print('na detected')
            continue
        print('This buoy is ', ith_buoy, row.wmo,  row.line_times, row.line_coords)
        color = matplotlib.colors.rgb2hex(cmap(ith_buoy/num_colors))
        feature =  { "type": "Feature", 
                    "geometry": { "type": "LineString", 
                                 "coordinates": row.line_coords, },
                    "properties": { "times": row.line_times, 
                                   "style": { "color": color, "weight": 3}, 
                                   'icon': 'circle',
                                   'iconstyle':{
                                       'fillColor': color,
                                       'opacity': 0.9,
                                       'stroke': False,
                                       'radius':5 
                                   },
                                   'popup': f'Buoy ID: {row.wmo}, \n Date: {row.date}',#, Date uploaded: {row.date_update}',
                                  },
                   }
        features.append(feature)
features

This buoy is  0 6902957 ('2020-06-01 03:18:00', '2020-06-11 03:24:00') ((-57.714, 7.773), (-57.743, 7.786))
This buoy is  0 6902957 ('2020-06-11 03:24:00', '2020-06-21 03:20:30') ((-57.743, 7.786), (-57.753, 7.782))
This buoy is  0 6902957 ('2020-06-21 03:20:30', '2020-07-01 03:14:00') ((-57.753, 7.782), (-57.78, 7.793))
This buoy is  0 6902957 ('2020-07-01 03:14:00', '2020-07-11 03:18:00') ((-57.78, 7.793), (-57.791, 7.805))
This buoy is  0 6902957 ('2020-07-11 03:18:00', '2020-07-21 03:13:00') ((-57.791, 7.805), (-57.799, 7.807))
This buoy is  0 6902957 ('2020-07-21 03:13:00', '2020-07-31 03:21:00') ((-57.799, 7.807), (-57.807, 7.811))
This buoy is  0 6902957 ('2020-07-31 03:21:00', '2020-08-10 03:20:30') ((-57.807, 7.811), (-57.825, 7.808))
This buoy is  0 6902957 ('2020-08-10 03:20:30', '2020-08-20 03:19:00') ((-57.825, 7.808), (-57.866, 7.811))
This buoy is  0 6902957 ('2020-08-20 03:19:00', '2020-08-30 03:18:00') ((-57.866, 7.811), (-57.89, 7.8))
This buoy is  0 6902957 ('2020-08

[{'type': 'Feature',
  'geometry': {'type': 'LineString',
   'coordinates': ((-57.714, 7.773), (-57.743, 7.786))},
  'properties': {'times': ('2020-06-01 03:18:00', '2020-06-11 03:24:00'),
   'style': {'color': '#ff0000', 'weight': 3},
   'icon': 'circle',
   'iconstyle': {'fillColor': '#ff0000',
    'opacity': 0.9,
    'stroke': False,
    'radius': 5},
   'popup': 'Buoy ID: 6902957, \n Date: 2020-06-11 03:24:00'}},
 {'type': 'Feature',
  'geometry': {'type': 'LineString',
   'coordinates': ((-57.743, 7.786), (-57.753, 7.782))},
  'properties': {'times': ('2020-06-11 03:24:00', '2020-06-21 03:20:30'),
   'style': {'color': '#ff0000', 'weight': 3},
   'icon': 'circle',
   'iconstyle': {'fillColor': '#ff0000',
    'opacity': 0.9,
    'stroke': False,
    'radius': 5},
   'popup': 'Buoy ID: 6902957, \n Date: 2020-06-21 03:20:30'}},
 {'type': 'Feature',
  'geometry': {'type': 'LineString',
   'coordinates': ((-57.753, 7.782), (-57.78, 7.793))},
  'properties': {'times': ('2020-06-21 03:20

# map it 

In [39]:
# https://github.com/python-visualization/folium/blob/master/folium/plugins/timestamped_geo_json.py
# https://nbviewer.jupyter.org/github/python-visualization/folium/tree/master/examples/
# https://www.linkedin.com/pulse/visualizing-nyc-bike-data-interactive-animated-maps-folium-toso
# https://python-visualization.github.io/folium/modules.html

m = folium.Map(location=start_longlat, zoom_start=4)#, width=800, height=300)
plugins.TimestampedGeoJson(
    { "type": "FeatureCollection", "features": features},
    period="P1D", add_last_point=True, 
    duration = 'P2M',
    min_speed = 1,
    max_speed = 50,
    transition_time = 100, # in millisec
).add_to(m)

m

In [28]:
txt = '<tbody _ngcontent-alb-c13=""><!----><tr _ngcontent-alb-c13="" class="ng-star-inserted" style=""><td _ngcontent-alb-c13="" class="border-l border-orange"></td><td _ngcontent-alb-c13=""><a _ngcontent-alb-c13="" href="/float/4900209">4900209</a></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><span _ngcontent-alb-c13="" class="light"><strong _ngcontent-alb-c13="">OIN-02-F2-009</strong>10008</span></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted">PROVOR</td><!----><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><div _ngcontent-alb-c13="" style="display: flex;"><div _ngcontent-alb-c13=""> 27/11/2003<br _ngcontent-alb-c13=""><span _ngcontent-alb-c13="" class="light">03:32:00</span></div><!----></div></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted">62</td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><div _ngcontent-alb-c13="" style="display: flex;"><div _ngcontent-alb-c13=""><svg-icon-battery _ngcontent-alb-c13="" _nghost-alb-c29="" class="green"><svg _ngcontent-alb-c29="" viewBox="0 0 9 17"><path _ngcontent-alb-c29="" d="M6.936,1.6l-1.336,0l0,-1.6l-3.2,0l0,1.6l-1.336,0c-0.583,0.003 -1.061,0.481 -1.064,1.064l0,12.264c-0.001,0.585 0.479,1.069 1.064,1.072l5.864,0c0.585,0.001 1.069,-0.479 1.072,-1.064l0,-12.272c-0.003,-0.583 -0.481,-1.061 -1.064,-1.064Z"></path></svg></svg-icon-battery>  </div><!----></div></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><span _ngcontent-alb-c13="" class="light">14/03/2002</span></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><div _ngcontent-alb-c13=""></div></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><div _ngcontent-alb-c13="" style="display: flex;"><div _ngcontent-alb-c13="">  </div><!----></div></td><td _ngcontent-alb-c13=""><div _ngcontent-alb-c13="" style="display: flex;"><div _ngcontent-alb-c13=""> <br _ngcontent-alb-c13=""><span _ngcontent-alb-c13="" class="light"></span></div><!----></div></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><div _ngcontent-alb-c13="" style="display: flex;"><div _ngcontent-alb-c13="">H</div><!----><div _ngcontent-alb-c13="" applabeltooltip="" class="alert-flag-container ng-star-inserted"><span _ngcontent-alb-c13="" class="fa fa-exclamation-triangle warning-alert-flag"></span></div></div></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><div _ngcontent-alb-c13="" style="display: flex;"><div _ngcontent-alb-c13=""> </div><!----></div></td><!----><!----><!----><!----><!----><!----><!----><!----><!----><!----></tr><tr _ngcontent-alb-c13="" class="ng-star-inserted" style=""><td _ngcontent-alb-c13="" class="border-l border-green"></td><td _ngcontent-alb-c13=""><a _ngcontent-alb-c13="" href="/float/4900183">4900183</a></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><span _ngcontent-alb-c13="" class="light"><strong _ngcontent-alb-c13="">00151</strong>07274</span></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted">SOLO_W</td><!----><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><div _ngcontent-alb-c13="" style="display: flex;"><div _ngcontent-alb-c13=""> 08/10/2004<br _ngcontent-alb-c13=""><span _ngcontent-alb-c13="" class="light">04:30:44</span></div><!----></div></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted">87</td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><div _ngcontent-alb-c13="" style="display: flex;"><div _ngcontent-alb-c13=""><svg-icon-battery _ngcontent-alb-c13="" _nghost-alb-c29="" class="green"><svg _ngcontent-alb-c29="" viewBox="0 0 9 17"><path _ngcontent-alb-c29="" d="M6.936,1.6l-1.336,0l0,-1.6l-3.2,0l0,1.6l-1.336,0c-0.583,0.003 -1.061,0.481 -1.064,1.064l0,12.264c-0.001,0.585 0.479,1.069 1.064,1.072l5.864,0c0.585,0.001 1.069,-0.479 1.072,-1.064l0,-12.272c-0.003,-0.583 -0.481,-1.061 -1.064,-1.064Z"></path></svg></svg-icon-battery>  </div><!----></div></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><span _ngcontent-alb-c13="" class="light">20/05/2002</span></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><div _ngcontent-alb-c13=""></div></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><div _ngcontent-alb-c13="" style="display: flex;"><div _ngcontent-alb-c13="">  </div><!----></div></td><td _ngcontent-alb-c13=""><div _ngcontent-alb-c13="" style="display: flex;"><div _ngcontent-alb-c13=""> <br _ngcontent-alb-c13=""><span _ngcontent-alb-c13="" class="light"></span></div><!----></div></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><div _ngcontent-alb-c13="" style="display: flex;"><div _ngcontent-alb-c13=""></div><!----></div></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><div _ngcontent-alb-c13="" style="display: flex;"><div _ngcontent-alb-c13=""> </div><!----></div></td><!----><!----><!----><!----><!----><!----><!----><!----><!----><!----></tr><tr _ngcontent-alb-c13="" class="ng-star-inserted" style=""><td _ngcontent-alb-c13="" class="border-l border-green"></td><td _ngcontent-alb-c13=""><a _ngcontent-alb-c13="" href="/float/4900181">4900181</a></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><span _ngcontent-alb-c13="" class="light"><strong _ngcontent-alb-c13="">00133</strong>27276</span></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted">SOLO_W</td><!----><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><div _ngcontent-alb-c13="" style="display: flex;"><div _ngcontent-alb-c13=""> 18/05/2003<br _ngcontent-alb-c13=""><span _ngcontent-alb-c13="" class="light">21:45:00</span></div><!----></div></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted">50</td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><div _ngcontent-alb-c13="" style="display: flex;"><div _ngcontent-alb-c13=""><svg-icon-battery _ngcontent-alb-c13="" _nghost-alb-c29="" class="green"><svg _ngcontent-alb-c29="" viewBox="0 0 9 17"><path _ngcontent-alb-c29="" d="M6.936,1.6l-1.336,0l0,-1.6l-3.2,0l0,1.6l-1.336,0c-0.583,0.003 -1.061,0.481 -1.064,1.064l0,12.264c-0.001,0.585 0.479,1.069 1.064,1.072l5.864,0c0.585,0.001 1.069,-0.479 1.072,-1.064l0,-12.272c-0.003,-0.583 -0.481,-1.061 -1.064,-1.064Z"></path></svg></svg-icon-battery>  </div><!----></div></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><span _ngcontent-alb-c13="" class="light">22/02/2002</span></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><div _ngcontent-alb-c13=""></div></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><div _ngcontent-alb-c13="" style="display: flex;"><div _ngcontent-alb-c13="">  </div><!----></div></td><td _ngcontent-alb-c13=""><div _ngcontent-alb-c13="" style="display: flex;"><div _ngcontent-alb-c13=""> <br _ngcontent-alb-c13=""><span _ngcontent-alb-c13="" class="light"></span></div><!----></div></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><div _ngcontent-alb-c13="" style="display: flex;"><div _ngcontent-alb-c13=""></div><!----></div></td><!----><td _ngcontent-alb-c13="" class="ng-star-inserted"><div _ngcontent-alb-c13="" style="display: flex;"><div _ngcontent-alb-c13=""> </div><!----></div></td><!----><!----><!----><!----><!----><!----><!----><!----><!----><!----></tr><tr _ngcontent-alb-c13="" class="ng-star-inserted" style=""><td _ngcontent-alb-c13="" class="border-l border-green"></td><td _ngcontent-alb-c13=""><a _ngcontent-alb-c13="" href="/float/4900186">4900186</a>'

In [40]:
m.save(f'atlantic_2mo_trails_{TIME_START}-{TIME_END}.html')